## Recursive Least Square with Kafka and Spark streaming 

This notebook provides an example for estimating the coefficients of a linear model on streaming data coming from a Kafka producer. The coefficient estimation is achieved using the recursive least square (RLS) algorithm, using two different RLS models in parallel (with different forgetting factors).

The linear model has 10 parameters, with coefficients [1,0,0,0,0,0,0,0,0,1] (see notebook KafkaSendRLS).

This notebook uses 
* the [Python client for the Apache Kafka distributed stream processing system](http://kafka-python.readthedocs.io/en/master/index.html) to receive messages from a Kafka cluster. 
* [Spark streaming](https://spark.apache.org/docs/latest/streaming-programming-guide.html) for processing the streaming data



### General import

In [1]:
import time
import re, ast
import numpy as np
import os

### Start Spark session


In [2]:
from pyspark.sql import SparkSession
from pyspark.streaming import StreamingContext
from pyspark.streaming.kafka import KafkaUtils

os.environ['PYSPARK_SUBMIT_ARGS'] = '--conf spark.ui.port=4040 '+\
                                '--packages org.apache.spark:spark-streaming-kafka-0-8_2.11:2.2.1 '+\
                                '--conf spark.driver.memory=2g  pyspark-shell'

spark = SparkSession \
    .builder \
    .master("local[2]") \
    .appName("KafkaReceive") \
    .getOrCreate()

### Connect to Kafka cluster on topic dataLinearModel

In [3]:
#This function creates a connection to a Kafka stream
#You may change the topic, or batch interval
#The Zookeeper server is assumed to be running at 127.0.0.1:2181
#The function returns the Spark context, Spark streaming context, and DStream object
def getKafkaDStream(spark,topic='persistence',batch_interval=10):

    #Get Spark context
    sc=spark.sparkContext

    #Create streaming context, with required batch interval
    ssc = StreamingContext(sc, batch_interval)

    #Checkpointing needed for stateful transforms
    ssc.checkpoint("checkpoint")
    
    #Create a DStream that represents streaming data from Kafka, for the required topic 
    dstream = KafkaUtils.createStream(ssc, "127.0.0.1:2181", "spark-streaming-consumer", {topic: 1})
    
    return [sc,ssc,dstream]


In [4]:
def updateFunction(new_values, state): 
    ## RLS update function
    ## Only update with first value of RDD. You should transofrm new_values to array, and update models for all values 
    if (len(new_values)>0 ):
        
        key=new_values[0][0]
        yx=new_values[0][1]
        i=yx[0]
        y=yx[1]
        x=yx[2:]
        n=len(x)
        
        beta=state[1]
        beta.shape=(n,1)
        V=state[2]
        mu=state[3]
        sse=state[4]  ## sum of squared errors
        N=state[5]   ## number of treated samples
        x.shape=(1,n)
        err=y-x.dot(beta)
        sse=sse+pow(err,2.0)
        V=1.0/mu*(V-V.dot(x.T).dot(x).dot(V)/(1.0+float(x.dot(V).dot(x.T))))
        gamma=V.dot(x.T)
        beta=beta+gamma*err
        
        return (key,beta,V,mu,sse/(N+1.0),N+1)  ## update formula mod1
        
    else:
        return state

### Define streaming pipeline

* We define a stream with two states, for updating two RLS models in paralell. Each state contains a state of variables to keep the state of the model, as well as to keep track of MSE estimates. A state is a list of 5 elements:
    * The first three are beta, V and mu, and define the state of the model (see RLS formulas in course)
    * The last two are an estimate of the MSE of the model, and the number of treated samples 
* We create a DStream, flat map with the sensor ID as key, update state for the stream, and save MSE

In [5]:
import re, ast

n=10 # number of features

beta1=np.zeros(n)  ## initial parameter vector for model 1
V1=np.diag(np.zeros(n)+10) ## initial covariance matrix for model 1
mu1=1.0 # forgetting factor for model 1

state1=('mod1',beta1,V1,mu1,0,0)

beta2=np.zeros(n)  ## initial parameter vector for model 2
V2=np.diag(np.zeros(n)+1) ## initial covariance matrix for model 2
mu2=0.99 # forgetting factor for model 2

state2=('mod2',beta2,V2,mu2,0,0)

[sc,ssc,dstream]=getKafkaDStream(spark=spark,topic='dataLinearModel',batch_interval=1)

#Evaluate input (a list - see KafkaSendRLS notebook)
dstream = dstream.map(lambda x: np.array(ast.literal_eval(x[1])))
#dstream.pprint()

dstream=dstream.flatMap(lambda x: [('mod1',('mod1',1.0*np.array(x))),
                            ('mod2',('mod2',1.0*np.array(x)))])
#dstream.pprint()

initialStateRDD = sc.parallelize([(u'mod1', state1),
                                  (u'mod2', state2)])

dstream=dstream.updateStateByKey(updateFunction,initialRDD=initialStateRDD)

#Only display beta and error
#beta should converge to [1,0,0,0,0,0,0,0,0,1] (send KafkaSend notebook)
dstream.map(lambda x: x[1][0:2]+x[1][4:6]).pprint()
#dstream.pprint()

### Start streaming application

In [6]:
ssc.start()

-------------------------------------------
Time: 2018-05-09 10:25:42
-------------------------------------------
('mod1', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)
('mod2', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)

-------------------------------------------
Time: 2018-05-09 10:25:43
-------------------------------------------
('mod1', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)
('mod2', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)

-------------------------------------------
Time: 2018-05-09 10:25:44
-------------------------------------------
('mod1', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)
('mod2', array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]), 0, 0)

-------------------------------------------
Time: 2018-05-09 10:25:45
-------------------------------------------
('mod1', array([[ 0.04935249],
       [ 0.38071164],
       [ 0.28676416],
       [ 0.43319835],


-------------------------------------------
Time: 2018-05-09 10:25:57
-------------------------------------------
('mod1', array([[-0.03974507],
       [ 0.80644721],
       [ 0.24482463],
       [-0.02945066],
       [ 0.21766352],
       [ 0.04158346],
       [ 0.12401061],
       [-0.05645939],
       [ 0.10156831],
       [ 0.81382732]]), array([[ 0.00019086]]), 13)
('mod2', array([[ -5.85531075e-03],
       [  5.73373220e-01],
       [  3.23293181e-01],
       [  5.83191115e-05],
       [  2.79402422e-01],
       [  7.23201468e-02],
       [  2.46170349e-01],
       [  2.64195827e-02],
       [  6.95258761e-02],
       [  6.11103076e-01]]), array([[ 0.00060374]]), 13)

-------------------------------------------
Time: 2018-05-09 10:25:58
-------------------------------------------
('mod1', array([[-0.01676903],
       [ 0.87028548],
       [ 0.18832993],
       [-0.03578443],
       [ 0.19711621],
       [ 0.01996242],
       [ 0.09859523],
       [ 0.04337075],
       [ 0.0096263

-------------------------------------------
Time: 2018-05-09 10:26:10
-------------------------------------------
('mod1', array([[ 0.02382381],
       [ 0.98430124],
       [ 0.00617353],
       [-0.00801687],
       [ 0.03386811],
       [ 0.01146989],
       [ 0.02179597],
       [ 0.0683784 ],
       [-0.02218484],
       [ 0.96795952]]), array([[  5.02682769e-05]]), 26)
('mod2', array([[ 0.04155271],
       [ 0.76915997],
       [ 0.06187529],
       [ 0.01165956],
       [ 0.13019637],
       [ 0.04289109],
       [ 0.08084526],
       [ 0.08588622],
       [ 0.01217053],
       [ 0.79458431]]), array([[ 0.00024611]]), 26)

-------------------------------------------
Time: 2018-05-09 10:26:11
-------------------------------------------
('mod1', array([[ 0.02197626],
       [ 0.98950677],
       [ 0.01016679],
       [-0.00587901],
       [ 0.03375955],
       [ 0.00803966],
       [ 0.02177533],
       [ 0.06887086],
       [-0.02327741],
       [ 0.96487264]]), array([[  2.88040

-------------------------------------------
Time: 2018-05-09 10:26:23
-------------------------------------------
('mod1', array([[ 0.01553025],
       [ 0.99950482],
       [ 0.01432202],
       [-0.00313668],
       [ 0.0206026 ],
       [ 0.0112254 ],
       [ 0.01403035],
       [ 0.06200888],
       [-0.0139657 ],
       [ 0.96855128]]), array([[  7.28508560e-06]]), 39)
('mod2', array([[ 0.02163916],
       [ 0.80762462],
       [ 0.03860014],
       [ 0.02298518],
       [ 0.08983096],
       [ 0.03680261],
       [ 0.0943259 ],
       [ 0.09603082],
       [-0.01497902],
       [ 0.86153669]]), array([[ 0.00013596]]), 39)

-------------------------------------------
Time: 2018-05-09 10:26:24
-------------------------------------------
('mod1', array([[ 0.01282561],
       [ 0.98502836],
       [ 0.01226549],
       [ 0.00219998],
       [ 0.02441913],
       [ 0.00958091],
       [ 0.02161243],
       [ 0.05450393],
       [-0.01333826],
       [ 0.97540782]]), array([[ 0.000104

-------------------------------------------
Time: 2018-05-09 10:26:36
-------------------------------------------
('mod1', array([[ 0.01743587],
       [ 0.99905668],
       [ 0.01102373],
       [ 0.0018001 ],
       [ 0.02386649],
       [ 0.01073427],
       [ 0.0069043 ],
       [ 0.03333636],
       [ 0.00516154],
       [ 0.98336288]]), array([[  2.00545868e-05]]), 52)
('mod2', array([[ 0.01027438],
       [ 0.89115647],
       [ 0.02850468],
       [ 0.00702488],
       [ 0.0676878 ],
       [ 0.03936794],
       [ 0.04212459],
       [ 0.05386813],
       [ 0.01581713],
       [ 0.90792116]]), array([[  7.29644465e-05]]), 52)

-------------------------------------------
Time: 2018-05-09 10:26:37
-------------------------------------------
('mod1', array([[ 0.01735239],
       [ 0.99944146],
       [ 0.0110351 ],
       [ 0.00302654],
       [ 0.02165895],
       [ 0.01285761],
       [ 0.00798525],
       [ 0.03332286],
       [ 0.00136413],
       [ 0.98654737]]), array([[  3.

...

-------------------------------------------
Time: 2018-05-09 11:51:11
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-02],
       [  2.37531155e-02],
       [  1.03193056e-02],
       [  9.98732706e-01]]), array([[  4.27624752e-05]]), 88)
('mod2', array([[-0.00156981],
       [ 0.93384911],
       [ 0.02725091],
       [ 0.01091385],
       [ 0.04058293],
       [ 0.02999896],
       [ 0.04118767],
       [ 0.02909496],
       [ 0.02699263],
       [ 0.95216437]]), array([[  8.60024069e-05]]), 88)

-------------------------------------------
Time: 2018-05-09 11:51:12
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-

-------------------------------------------
Time: 2018-05-09 11:51:23
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-02],
       [  2.37531155e-02],
       [  1.03193056e-02],
       [  9.98732706e-01]]), array([[  4.27624752e-05]]), 88)
('mod2', array([[-0.00156981],
       [ 0.93384911],
       [ 0.02725091],
       [ 0.01091385],
       [ 0.04058293],
       [ 0.02999896],
       [ 0.04118767],
       [ 0.02909496],
       [ 0.02699263],
       [ 0.95216437]]), array([[  8.60024069e-05]]), 88)

-------------------------------------------
Time: 2018-05-09 11:51:24
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-

-------------------------------------------
Time: 2018-05-09 11:51:35
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-02],
       [  2.37531155e-02],
       [  1.03193056e-02],
       [  9.98732706e-01]]), array([[  4.27624752e-05]]), 88)
('mod2', array([[-0.00156981],
       [ 0.93384911],
       [ 0.02725091],
       [ 0.01091385],
       [ 0.04058293],
       [ 0.02999896],
       [ 0.04118767],
       [ 0.02909496],
       [ 0.02699263],
       [ 0.95216437]]), array([[  8.60024069e-05]]), 88)

-------------------------------------------
Time: 2018-05-09 11:51:36
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-

-------------------------------------------
Time: 2018-05-09 11:51:47
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-02],
       [  2.37531155e-02],
       [  1.03193056e-02],
       [  9.98732706e-01]]), array([[  4.27624752e-05]]), 88)
('mod2', array([[-0.00156981],
       [ 0.93384911],
       [ 0.02725091],
       [ 0.01091385],
       [ 0.04058293],
       [ 0.02999896],
       [ 0.04118767],
       [ 0.02909496],
       [ 0.02699263],
       [ 0.95216437]]), array([[  8.60024069e-05]]), 88)

-------------------------------------------
Time: 2018-05-09 11:51:48
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-

-------------------------------------------
Time: 2018-05-09 11:51:59
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-02],
       [  2.37531155e-02],
       [  1.03193056e-02],
       [  9.98732706e-01]]), array([[  4.27624752e-05]]), 88)
('mod2', array([[-0.00156981],
       [ 0.93384911],
       [ 0.02725091],
       [ 0.01091385],
       [ 0.04058293],
       [ 0.02999896],
       [ 0.04118767],
       [ 0.02909496],
       [ 0.02699263],
       [ 0.95216437]]), array([[  8.60024069e-05]]), 88)

-------------------------------------------
Time: 2018-05-09 11:52:00
-------------------------------------------
('mod1', array([[  7.75306968e-03],
       [  9.99478050e-01],
       [  1.19862180e-02],
       [  5.88542523e-04],
       [  1.95431952e-02],
       [  1.24551411e-02],
       [  1.44379616e-

### Stop streaming

In [7]:
ssc.stop(stopSparkContext=False,stopGraceFully=False)

-------------------------------------------
Time: 2018-04-11 10:24:29
-------------------------------------------
('mod1', array([[ 0.22694852],
       [ 0.35408383],
       [ 0.00752181],
       [ 0.15257772],
       [ 0.01549361],
       [ 0.11455939],
       [ 0.41975984],
       [ 0.16142979],
       [ 0.38114068],
       [ 0.28878947]]), array([[ 0.07124946]]), 4)
('mod2', array([[ 0.1937677 ],
       [ 0.30240471],
       [ 0.07113931],
       [ 0.17484219],
       [ 0.11190291],
       [ 0.16065204],
       [ 0.29383222],
       [ 0.16671696],
       [ 0.29899335],
       [ 0.21592691]]), array([[ 0.0875207]]), 4)

